In [12]:
%reset -f

In [1]:
import glob
from matplotlib import pyplot
import numpy as np
from sklearn.preprocessing import MinMaxScaler
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.lines import Line2D
import pandas as pd

from sklearn.metrics import f1_score
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import precision_recall_fscore_support

import warnings
import os
import datetime
import time
import funcy
import copy
import random



In [2]:
warnings.filterwarnings("ignore")

In [3]:
# this is helper method for TS rendering with datapoints
# visualize FP and FN on time series
def ts_confusion_visualization(data_test, pred_val, dataset, filename, modelname):
    x, y, true_val = data_test['timestamp'].tolist(), data_test['value'].tolist(), data_test['is_anomaly'].tolist()
    try:
        x = [datetime.datetime.strptime(x, '%m/%d/%Y %H:%M') for x in x]
    except:
        try:
            x = [datetime.datetime.strptime(x, '%Y-%m-%d %H:%M:%S') for x in x]
        except:
            pass

    fp = [(x[i], y[i]) for i in range(len(true_val)) if true_val[i] == 0 and pred_val[i] == 1]
    fn = [(x[i], y[i]) for i in range(len(true_val)) if true_val[i] == 1 and pred_val[i] == 0]

    fig, ax = plt.subplots()
    ax.plot(x, y, color='grey', lw=0.5, zorder=0)
    ax.scatter([t[0] for t in fp], [t[1] for t in fp], color='r', s=5, zorder=5)
    ax.scatter([t[0] for t in fn], [t[1] for t in fn], color='y', s=5, zorder=5)

    legend_elements = [Line2D([0], [0], color='k', lw=2, label='Correct'),
                       Line2D([0], [0], marker='o', color='r', markersize=5, label='FP'),
                       Line2D([0], [0], marker='o', color='y', markersize=5, label='FN')]

    ax.legend(handles=legend_elements, loc='best')

    pyplot.savefig(f'../results/imgs/{modelname}_{dataset}_{filename}.png')
    pyplot.clf()
    pyplot.close('all')
    plt.close('all')
    del fig
    del ax

In [4]:
# function that finds the indexes of non-anomalies for interpolation 
def interpolation_indexes(mylist, mynumber):
    
    left_neighbour = 0
    right_neighbour = 0
    
    # check left neighbour
    if((mynumber - 1) not in mylist):
        left_neighbour = mynumber - 1
    else:
        min_number = mynumber
        while min_number in mylist:
            min_number = min_number - 1
        left_neighbour = min_number
    
    # check right neighbour
    if((mynumber + 1) not in mylist):
        right_neighbour = mynumber + 1
    else:
        max_number = mynumber
        while max_number in mylist:
            max_number = max_number + 1
        right_neighbour = max_number
    
    return left_neighbour, right_neighbour

In [15]:
def train_anomaly_removal(df_train):
    
    # extract indexes for anomalies
    indexes = list(df_train[df_train.is_anomaly == 1].index)

    # creating a new df that replaces the anomalous samples with interpolation value
    df = pd.DataFrame(columns = df_train.columns)
    print(df_train.shape)
    for i in range(0, df_train.shape[0]):

        #print(i)

        # add all non-anomalies
        if df_train.is_anomaly[i] == 0:
            df = df.append({'timestamp' : df_train.timestamp[i], 'value' : df_train.value[i], 'is_anomaly' : df_train.is_anomaly[i]},
            ignore_index = True)

        if df_train.is_anomaly[i] == 1:
            if (i+1) < df_train.shape[0] and df_train.is_anomaly[i+1] != 1:
                #print(i)
                value_interpolation = (df_train.value[interpolation_indexes(indexes, i)[0]]+df_train.value[interpolation_indexes(indexes, i)[1]])/2

                df = df.append({'timestamp' : df_train.timestamp[i], 'value': value_interpolation, 'is_anomaly' : 0.0},
            ignore_index = True)
    return df

# Set hyperparameters for train flow

In [6]:
model_name = 'pci'

# decide on windwos with Lorena
anomaly_window = 65
test_window = 65
for_optimization = False

use_drift_adapt = False
drift_detector = None
use_entropy = False
threshold_type = 'static'
if use_entropy:
    threshold_type = 'dynamic'

# TODO discuss averaging
# class averaging type for evaluation metrics calculations
# Calculate metrics globally by counting the total true positives, false negatives and false positives.
avg_type = None

# allowed delay for anomaly shifts during evaluation
evaluation_delay = 7

# Create FFT model

In [12]:
import sys
sys.path.insert(2, '../utils/')

from evaluation import label_evaluation
from fft import detect_anomalies
from dwt_mlead import DWT_MLEAD
from pci import PCIAnomalyDetector

# fft
ifft_parameters: int = 5
context_window_size: int = 21
local_outlier_threshold: float = .6
max_anomaly_window_size: int = 50
max_sign_change_distance: int = 10
random_state: int = 42

# dwt mlead
start_level: int = 3
quantile_epsilon: float = 0.01
random_state: int = 42
use_column_index: int = 0

# from the paper on their timeseries optimal (k,p)
# flactuates around (5, 0.95) and (7, 0.97) so we take approx them
window_size: int = 6
thresholding_p: float = 0.96

# Import SR model

In [8]:
from msanomalydetector import THRESHOLD, MAG_WINDOW, SCORE_WINDOW
from msanomalydetector import DetectMode
from msanomalydetector.spectral_residual import SpectralResidual

####################################################################################
# this code is taken from
# https://github.com/microsoft/anomalydetector
# with modifications to account for sliding windows and entropy thresholding
# the modified code is worj from:
# https://github.com/nata1y/tiny-anom-det/tree/main/models/sr
####################################################################################

# initial parameters from the paper
sr_model_params = (THRESHOLD, MAG_WINDOW, SCORE_WINDOW, 99)

# Run experiments

In [17]:
# 'Yahoo_A1Benchmark', 'NAB_realAWSCloudwatch', 'kpi'
for dataset in ['NAB_realAWSCloudwatch', 'Yahoo_A1Benchmark', 'kpi']:
    for training_type in ['static', 'sliding_window', 'full_history']:
        for model_name in ['sr', 'pci', 'fft', 'dwt_mlead']:
            
            try:
                stats_full = pd.read_csv(f'../results/scores/{model_name}_{dataset}_{training_type}_stats.csv')
            except:
                # set window size equals one week
                # yahoo is hourly, nab and kpi are 5 minute
                if dataset == 'Yahoo_A1Benchmark':
                    anomaly_window = 168
                else:
                    anomaly_window = 2016

                test_window = anomaly_window

                if dataset == 'kpi':
                    train_data_path = f'../datasets/kpi/train/'
                else:
                    train_data_path = f'../datasets/{dataset}/'

                for filename in os.listdir(train_data_path):
                    f = os.path.join(train_data_path, filename)
                    data = pd.read_csv(f, engine='python')

                    filename = filename.replace('.csv', '')
                    print(f'Working with current time series: {filename} in dataset {dataset}')

                    data.rename(columns={'timestamps': 'timestamp', 'anomaly': 'is_anomaly'}, inplace=True)
    #                 data.drop_duplicates(subset=['timestamp'], keep=False, inplace=True)

                    # timestamp preprocessing for kpi -- their are unix timestamps
                    if dataset == 'kpi':
                        data_test = pd.read_csv(os.path.join(f'../datasets/{dataset}/test/', filename + '.csv'))
                        data_test['timestamp'] = data_test['timestamp'].apply(
                            lambda x: datetime.datetime.utcfromtimestamp(x).strftime('%Y-%m-%d %H:%M:%S'))
                        data['timestamp'] = data['timestamp'].apply(
                            lambda x: datetime.datetime.utcfromtimestamp(x).strftime('%Y-%m-%d %H:%M:%S'))

                        # kpi stores train and test in different ts -- merge them into one to follow structure
                        data = pd.concat([data, data_test], ignore_index=True)

                    # 50-50 train/test split
                    data_train, data_test = np.array_split(data, 2)

                    # set (re)training (== application) windwos based on type
                    if training_type == 'static':
                        data_in_memory_size = anomaly_window
                    elif training_type == 'sliding_window':
                        data_in_memory_size = data_train.shape[0]
                    elif training_type == 'full_history':
                        data_in_memory_size = 0


                    # train model #######################################################################################
                    start = time.time()
                    fft_threshold = 0

                    if model_name == 'fft':
                        # since no threshold is provided, we are using the max on de-anomalized training set
                        # same tichnique is sued in dynamic models
                        data_train = train_anomaly_removal(data_train)
                        model = detect_anomalies
                        random.seed(random_state)
                        np.random.seed(random_state)
                        anomaly_scores = model(
                                        data_train['value'].to_numpy(),
                                        max_region_size=max_anomaly_window_size,
                                        local_neighbor_window=context_window_size
                                    )
                        fft_threshold = max(anomaly_scores)
                    elif model_name == 'pci':
                        model = PCIAnomalyDetector(
                            k=window_size // 2,
                            p=thresholding_p,
                            calculate_labels=False
                        )
                    elif model_name == 'sr':
                        model = SpectralResidual(series=data_train[['value', 'timestamp']], use_drift=use_drift_adapt,
                                        threshold=sr_model_params[0], mag_window=sr_model_params[1],
                                        score_window=sr_model_params[2], sensitivity=sr_model_params[3],
                                        detect_mode=DetectMode.anomaly_only, dataset=dataset,
                                        filename=filename, drift_detector=drift_detector,
                                        data_in_memory_sz=data_in_memory_size, anomaly_window=anomaly_window)
                        model.fit()

                    end_time = time.time()

                    diff = end_time - start
                    print(f"Trained SR on {filename} for {diff}")

                    # test model #########################################################################################

                    batch_metrices_f1_entropy = []
                    batch_metrices_f1_no_entropy = []
                    y_pred_total_no_entropy, y_pred_total_entropy = [], []
                    batches_with_anomalies = []
                    idx = 0

                    pred_time = []

                    if for_optimization:
                        data_in_memory = pd.DataFrame([])
                    else:
                        data_in_memory = copy.deepcopy(data_train)

                    for start in range(0, data_test.shape[0], anomaly_window):
                        try:
                            # current window on which TESTING and SCORING is applied
                            window = data_test.iloc[start:start + anomaly_window]
                            # data hold in memory, calculations and predictions are performed across this window
                            data_in_memory = pd.concat([data_in_memory, window])[-data_in_memory_size:]

                            X, y = window['value'], window['is_anomaly']
                            if y.tolist():
                                if model_name == 'fft':
                                    anomaly_scores = model(
                                        data_in_memory['value'].to_numpy(),
                                        max_region_size=max_anomaly_window_size,
                                        local_neighbor_window=context_window_size
                                    )
                                    # paper does not provide any way to detect anomaly threshold.
                                    # we use same as for lstm
                                    y_pred_noe = [1 if x > fft_threshold else 0 for x in anomaly_scores[-window.shape[0]:]]
                                elif model_name == 'sr':
                                    model.__series__ = data_in_memory
                                    try:
                                        res = model.predict(data_in_memory, window.shape[0])
                                        y_pred_noe = [1 if x else 0 for x in res['isAnomaly'].tolist()]
                                    except Exception as e:
                                        print(str(e))
                                        y_pred_noe = [0 for _ in range(window.shape[0])]
                                elif model_name == 'dwt_mlead':
                                    # FROM PAPER: 
                                    # We empirically determined the setting l = 5 for the NAB data and l = 7 for the A3 data
                                    if 'NAB' in dataset:
                                        start_level = 5
                                    elif 'Yahoo' in dataset:
                                        start_level = 7
                                    model = DWT_MLEAD(data_in_memory['value'].to_numpy(),
                                        start_level=start_level,
                                        quantile_boundary_type="percentile",
                                        quantile_epsilon=quantile_epsilon,
                                        track_coefs=True
                                    )
                                    anomaly_scores = model.detect()
                                    # FROM PAPER: 
                                    # We empirically determined the setting B = 3.5 for the NAB data and B = 1 for the A3 data
                                    threshold = 1
                                    if 'NAB' in dataset:
                                        threshold =  3.5
                                    y_pred_noe = [1 if x > threshold else 0 for x in anomaly_scores[-window.shape[0]:]]
                                elif model_name == 'pci':
                                    anomaly_scores, anomaly_labels = model.detect(data_in_memory['value'].to_numpy())
                                    print(anomaly_scores)
                                    print(anomaly_labels)
                                    y_pred_noe = anomaly_labels[-window.shape[0]:]

                                idx += 1
                                y_pred_total_no_entropy += [0 if val != 1 else 1 for val in funcy.lflatten(y_pred_noe)][:window.shape[0]]
                                y_pred_noe = y_pred_noe[:window.shape[0]]

                        except Exception as e:
                            raise e

                    # evaluate TS ########################################################################################

                    # calculate batched metrics per *test_window*
                    # for test stats we calculate F1 score for eacj class but use score for anomaly label 
                    # this works because we have binary classification
                    data_reset = data_test.reset_index()['is_anomaly']
                    for i in range(0, len(data_test['is_anomaly']), test_window):
                        # here, met_total will be (precision, recall, f1_score, support)

                        met_total = precision_recall_fscore_support(data_reset[i:i+test_window],
                                                                    y_pred_total_no_entropy[:data_test.shape[0]][i:i+test_window])
                        batch_metrices_f1_no_entropy.append(met_total[2][-1])

                    met_total_no_entropy = precision_recall_fscore_support(data_test['is_anomaly'],
                                                                    y_pred_total_no_entropy[:data_test.shape[0]])

                    # add entry to stats #######################################################################################

                    try:
                        stats_full = pd.read_csv(f'../results/scores/{model_name}_{dataset}_{training_type}_stats.csv')
                    except:
                        stats_full = pd.DataFrame([])

                    predicted_df = copy.deepcopy(data_test)
                    if use_entropy:
                        predicted_df['is_anomaly'] = y_pred_total_entropy
                    else:
                        predicted_df['is_anomaly'] = y_pred_total_no_entropy

                    smoothed_score = label_evaluation(data_test, predicted_df, evaluation_delay)
                    print(f'Smoothed F1 score is: {smoothed_score}')

                    stats_full = stats_full.append({
                        'model': model_name,
                        'ts_name': filename,
                        'window': anomaly_window,
                        'delay': evaluation_delay,
                        'f1_score': met_total_no_entropy[2][-1],
                        'f1_score_smoothed': smoothed_score,
                        'labels_true': data_test['is_anomaly'].tolist(),
                        'labels_pred': y_pred_total_no_entropy[:data_test.shape[0]]

                    }, ignore_index=True)
                    stats_full.to_csv(f'../results/scores/{model_name}_{dataset}_{training_type}_stats.csv', index=False)
                    print(f'My old F1 score is: {met_total_no_entropy[2][-1]}')

                    # plotting ##################################################################################################
                    # general on ts
                    if use_entropy:
                        ts_confusion_visualization(data_test, y_pred_total_entropy, dataset, filename, model_name)
                    else:
                        ts_confusion_visualization(data_test, y_pred_total_no_entropy, dataset, filename, model_name)


Working with current time series: ec2_cpu_utilization_24ae8d in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_24ae8d for 0.08800077438354492
Smoothed F1 score is: 0.15384615384615385
My old F1 score is: 0.15384615384615385
Working with current time series: ec2_cpu_utilization_53ea38 in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_53ea38 for 0.08893013000488281
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: ec2_cpu_utilization_5f5533 in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_5f5533 for 0.09299969673156738
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: ec2_cpu_utilization_77c1ca in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_77c1ca for 0.08999919891357422
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: ec2_cpu_utilization_825cc2 in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_825c

Working with current time series: rds_cpu_utilization_cc0c53 in dataset NAB_realAWSCloudwatch
Trained SR on rds_cpu_utilization_cc0c53 for 0.0
[2.774      2.28283333 0.27683333 ... 1.97920833 2.474675   8.28448333]
[0 0 0 ... 0 0 0]
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: rds_cpu_utilization_e47b3b in dataset NAB_realAWSCloudwatch
Trained SR on rds_cpu_utilization_e47b3b for 0.0
[7.70208333 5.48145833 0.961875   ... 1.580625   3.20979167 9.67145833]
[0 0 0 ... 0 0 0]
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: ec2_cpu_utilization_24ae8d in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_24ae8d for 0.0
Gaussion Distribution for level 5:
Shapes: mean=(2,), covariance=(2, 2), p=(63,)
Gaussion Distribution for level 5:
Shapes: mean=(2,), covariance=(2, 2), p=(63,)
Gaussion Distribution for level 6:
Shapes: mean=(2,), covariance=(2, 2), p=(31,)
Gaussion Distribution for level 6:
Shapes: mean=

Working with current time series: ec2_cpu_utilization_fe7f93 in dataset NAB_realAWSCloudwatch
Trained SR on ec2_cpu_utilization_fe7f93 for 0.0
Gaussion Distribution for level 5:
Shapes: mean=(2,), covariance=(2, 2), p=(63,)
Gaussion Distribution for level 5:
Shapes: mean=(2,), covariance=(2, 2), p=(63,)
Gaussion Distribution for level 6:
Shapes: mean=(2,), covariance=(2, 2), p=(31,)
Gaussion Distribution for level 6:
Shapes: mean=(2,), covariance=(2, 2), p=(31,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2

Working with current time series: grok_asg_anomaly in dataset NAB_realAWSCloudwatch
Trained SR on grok_asg_anomaly for 0.0
Gaussion Distribution for level 5:
Shapes: mean=(2,), covariance=(2, 2), p=(63,)
Gaussion Distribution for level 5:
Shapes: mean=(2,), covariance=(2, 2), p=(63,)
Gaussion Distribution for level 6:
Shapes: mean=(2,), covariance=(2, 2), p=(31,)
Gaussion Distribution for level 6:
Shapes: mean=(2,), covariance=(2, 2), p=(31,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2

Smoothed F1 score is: 0.05555555555555556
My old F1 score is: 0.05555555555555556
Working with current time series: elb_request_count_8c0756 in dataset NAB_realAWSCloudwatch
Trained SR on elb_request_count_8c0756 for 0.08999872207641602
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: grok_asg_anomaly in dataset NAB_realAWSCloudwatch
Trained SR on grok_asg_anomaly for 0.10600018501281738
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: iio_us-east-1_i-a2eb1cd9_NetworkIn in dataset NAB_realAWSCloudwatch
Trained SR on iio_us-east-1_i-a2eb1cd9_NetworkIn for 0.02800464630126953
Smoothed F1 score is: 0.0
My old F1 score is: 0.0
Working with current time series: rds_cpu_utilization_cc0c53 in dataset NAB_realAWSCloudwatch
Trained SR on rds_cpu_utilization_cc0c53 for 0.08696317672729492
Smoothed F1 score is: 0.16666666666666669
My old F1 score is: 0.16666666666666669
Working with current time series: rds_cpu_utilization_e47b

...

Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 

Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 7:

Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:


Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 8:
Shapes: mean=(2,), covariance=(2, 2), p=(7,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 9:
Shapes: mean=(2,), covariance=(2, 2), p=(3,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 10:
Shapes: mean=(2,), covariance=(2, 2), p=(1,)
Gaussion Distribution for level 7:
Shapes: mean=(2,), covariance=(2, 2), p=(15,)
Gaussion Distribution for level 7

KeyboardInterrupt: 